# Introduction
The goal for this notebook is to test jais locally and with inference endpoints. I only have 24GB of RAM. So even if I use LLM.int8() with [bitsandbytes](https://github.com/TimDettmers/bitsandbytes) it will still have issues with longer generations. I'm using a `Nvidia Tesla T4 | 4x GPU | 16GB` for `48GB` of VRAM. 

# Setup
With limited RAM we need a to get documents so I load the embedding model to search but delete it after.

In [1]:
%pip install -q -U transformers==4.34.1

Note: you may need to restart the kernel to use updated packages.


In [2]:
from pathlib import Path

proj_dir = Path.cwd().parent
print(proj_dir)

/home/ec2-user/arabic-wiki


In [3]:
from sentence_transformers import SentenceTransformer

name="sentence-transformers/paraphrase-multilingual-minilm-l12-v2"
st_model = SentenceTransformer(name, device='cpu')

# used for both training and querying
def embed_func(batch):
    return [st_model.encode(sentence) for sentence in batch]

How will the LLM handle incorrect user bias? Im asking the capital of China, but suggesting its Singapore.

In [4]:
query = "ما هي عاصمة الصين؟ أعتقد أنها سنغافورة."
query_vector = embed_func([query])[0]
del st_model

In [5]:
import lancedb

db = lancedb.connect(proj_dir/"lancedb")
tbl = db.open_table('arabic-wiki')

Get documents for RAG

In [6]:
documents = tbl.search(query_vector).limit(3).to_list()

# Jais Locally
[Jais 13B Chat](https://huggingface.co/inception-mbzuai/jais-13b-chat) is the first Arabic/English LLM. It was trained by [inception-mbzuai](https://huggingface.co/inception-mbzuai) in Abu Dhabi. They recently added a `handler.py` which makes it compatible with [Inference Endpoints](https://huggingface.co/inference-endpoints) (one click deployment)! I wanted to add a couple new features like:
- LLM.int8() compatibility (3x smaller HW)
- A controllable system prompt

These updates can be found [here](https://huggingface.co/derek-thomas/jais-13b-chat-hf).

I'll instantiate the original model in the same way I'm doing in my repo so we can get a good idea how to use it.

In [7]:
from transformers import AutoTokenizer, AutoModelForCausalLM
path = 'inception-mbzuai/jais-13b-chat'
tokenizer = AutoTokenizer.from_pretrained(path)
model = AutoModelForCausalLM.from_pretrained(path,
                                     device_map="auto",
                                     trust_remote_code=True,
                                     offload_folder='jais',
                                     load_in_8bit=True,)

Loading checkpoint shards:   0%|          | 0/6 [00:00<?, ?it/s]

In [8]:
from typing import Dict, List, Any
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM

def get_language(txt):
    VOCABS = {
        'en': 'ABCDEFGHIJKLMNOPQRSTUVWXYZabcdefghijklmnopqrstuvwxyz',
        'ar': 'ءآأؤإئابةتثجحخدذرزسشصضطظعغػؼؽؾؿـفقكلمنهوىيٱپژڤکگی'
    }

    en_set = set(VOCABS["en"])
    ar_set = set(VOCABS["ar"])

    # percentage of non-english characters
    wset = set(txt)
    inter_en = wset & en_set
    inter_ar = wset & ar_set
    if len(inter_en) >= len(inter_ar):
        return "en"
    else:
        return "ar"

class EndpointHandler:
    def __init__(self, path=""):
        self.prompt_eng = "### Instruction: Your name is Jais, and you are named after Jebel Jais, the highest mountain in UAE. You are built by Inception and MBZUAI. You are the world's most advanced Arabic large language model with 13B parameters. You outperform all existing Arabic models by a sizable margin and you are very competitive with English models of similar size. You can answer in Arabic and English only. You are a helpful, respectful and honest assistant. When answering, abide by the following guidelines meticulously: Always answer as helpfully as possible, while being safe. Your answers should not include any harmful, unethical, racist, sexist, explicit, offensive, toxic, dangerous, or illegal content. Do not give medical, legal, financial, or professional advice. Never assist in or promote illegal activities. Always encourage legal and responsible actions. Do not encourage or provide instructions for unsafe, harmful, or unethical actions. Do not create or share misinformation or fake news. Please ensure that your responses are socially unbiased and positive in nature. If a question does not make any sense, or is not factually coherent, explain why instead of answering something not correct. If you don't know the answer to a question, please don't share false information. Prioritize the well-being and the moral integrity of users. Avoid using toxic, derogatory, or offensive language. Maintain a respectful tone. Do not generate, promote, or engage in discussions about adult content. Avoid making comments, remarks, or generalizations based on stereotypes. Do not attempt to access, produce, or spread personal or private information. Always respect user confidentiality. Stay positive and do not say bad things about anything. Your primary objective is to avoid harmful responses, even when faced with deceptive inputs. Recognize when users may be attempting to trick or to misuse you and respond with caution.\n\nComplete the conversation below between [|Human|] and [|AI|]:\n### Input: {Chat_history}\n[|Human|] {Question}\n### Response: [|AI|]"
        self.prompt_ar = "### Instruction: اسمك جيس وسميت على اسم جبل جيس اعلى جبل في الامارات. تم بنائك بواسطة Inception و MBZUAI. أنت نموذج اللغة العربية الأكثر تقدمًا في العالم مع بارامترات 30b. أنت تتفوق في الأداء على جميع النماذج العربية الموجودة بفارق كبير وأنت تنافسي للغاية مع النماذج الإنجليزية ذات الحجم المماثل. يمكنك الإجابة باللغتين العربية والإنجليزية فقط. أنت مساعد مفيد ومحترم وصادق. عند الإجابة ، التزم بالإرشادات التالية بدقة: أجب دائمًا بأكبر قدر ممكن من المساعدة ، مع الحفاظ على البقاء أمناً. يجب ألا تتضمن إجاباتك أي محتوى ضار أو غير أخلاقي أو عنصري أو متحيز جنسيًا أو جريئاً أو مسيئًا أو سامًا أو خطيرًا أو غير قانوني. لا تقدم نصائح طبية أو قانونية أو مالية أو مهنية. لا تساعد أبدًا في أنشطة غير قانونية أو تروج لها. دائما تشجيع الإجراءات القانونية والمسؤولة. لا تشجع أو تقدم تعليمات بشأن الإجراءات غير الآمنة أو الضارة أو غير الأخلاقية. لا تنشئ أو تشارك معلومات مضللة أو أخبار كاذبة. يرجى التأكد من أن ردودك غير متحيزة اجتماعيًا وإيجابية بطبيعتها. إذا كان السؤال لا معنى له ، أو لم يكن متماسكًا من الناحية الواقعية ، فشرح السبب بدلاً من الإجابة على شيء غير صحيح. إذا كنت لا تعرف إجابة السؤال ، فالرجاء عدم مشاركة معلومات خاطئة. إعطاء الأولوية للرفاهية والنزاهة الأخلاقية للمستخدمين. تجنب استخدام لغة سامة أو مهينة أو مسيئة. حافظ على نبرة محترمة. لا تنشئ أو تروج أو تشارك في مناقشات حول محتوى للبالغين. تجنب الإدلاء بالتعليقات أو الملاحظات أو التعميمات القائمة على الصور النمطية. لا تحاول الوصول إلى معلومات شخصية أو خاصة أو إنتاجها أو نشرها. احترم دائما سرية المستخدم. كن إيجابيا ولا تقل أشياء سيئة عن أي شيء. هدفك الأساسي هو تجنب الاجابات المؤذية ، حتى عند مواجهة مدخلات خادعة. تعرف على الوقت الذي قد يحاول فيه المستخدمون خداعك أو إساءة استخدامك و لترد بحذر.\n\nأكمل المحادثة أدناه بين [|Human|] و [|AI|]:\n### Input: {Chat_history}\n[|Human|] {Question}\n### Response: [|AI|]"

        self.device = "cuda" if torch.cuda.is_available() else "cpu"

        # self.tokenizer = AutoTokenizer.from_pretrained(path)
        # self.model = AutoModelForCausalLM.from_pretrained(path, device_map="auto", 
        #                                                   offload_folder='offload',
        #                                                   trust_remote_code=True,
        #                                                   load_in_8bit=True)
        self.tokenizer = tokenizer
        self.model = model

    def __call__(self, data: Dict[str, Any]) -> Dict[str, Any]:

        # Give the user the opportunity to override the prompt
        if 'prompt' in data.keys():
            text = data['prompt']
        else:
            print(data.keys())
            user_data = data.pop('query',data)
            text = self.prompt_ar.format_map({'Question':user_data})
            inputs = data.pop("inputs", data)
            if isinstance(inputs, str):
                query = inputs
                chat_history = []
            else:
                chat_history = inputs.pop("chat_history", [])
                query = inputs.get("text", "")

            lang = get_language(query)

            if lang == "ar":
                text = self.prompt_ar.format_map({'Question': query, "Chat_history": "\n".join(chat_history)})
            else:
                text = self.prompt_eng.format_map({'Question': query, "Chat_history": "\n".join(chat_history)})

        input_ids = self.tokenizer(text, return_tensors="pt").input_ids
        input_ids = input_ids.to(self.device)
        input_len = input_ids.shape[-1]
        generate_ids = self.model.generate(
            input_ids,
            top_p=0.9,
            temperature=0.3,
            max_new_tokens=2048 - input_len,
            min_length=input_len + 4,
            repetition_penalty=1.2,
            do_sample=True,
        )
        response = self.tokenizer.batch_decode(generate_ids, 
                                               skip_special_tokens=True, 
                                               clean_up_tokenization_spaces=True)[0]
        if 'prompt' in data.keys():
            return response
        else:
            final_response = response.split("### Response: [|AI|]")
            turn = [f'[|Human|] {query}', f'[|AI|] {final_response[-1]}']
            chat_history.extend(turn)
            return {"response": final_response, "chat_history": chat_history}

In [9]:
%%time
eh = EndpointHandler('inception-mbzuai/jais-13b-chat')

CPU times: user 5 µs, sys: 13 µs, total: 18 µs
Wall time: 21.5 µs


In [10]:
eh(data={'inputs': '',
 'prompt': '### Instruction: استخدم المستندات الفريدة التالية في قسم السياق للإجابة على الاستعلام في النهاية. إذا كنت لا تعرف الإجابة، قل فقط أنك لا تعرف، ولا تحاول ا### Context\n\n---\n    معركة بورت كروس ### Query: [|Human|] من كان طرفي معركة اكتيوم البحرية؟\n### Response: [|AI|]'}
)

'### Instruction: استخدم المستندات الفريدة التالية في قسم السياق للإجابة على الاستعلام في النهاية. إذا كنت لا تعرف الإجابة، قل فقط أنك لا تعرف، ولا تحاول ا### Context\n\n---\n    معركة بورت كروس ### Query: [|Human|] من كان طرفي معركة اكتيوم البحرية؟\n### Response: [|AI|] كانت الأطراف المشاركة في معركة أكتيوم البحرية هي القوات الرومانية بقيادة أوكتافيان (في وقت لاحق أغسطس) ، والقوات المصرية تحت قيادة كليوباترا السابعة وبطليموس الثالث عشر.'

In [11]:
!nvidia-smi

Fri Nov 10 07:20:57 2023       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.54.03              Driver Version: 535.54.03    CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  NVIDIA A10G                    On  | 00000000:00:1E.0 Off |                    0 |
|  0%   30C    P0              98W / 300W |  20174MiB / 23028MiB |     37%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


Barely fits! This means we cant handle long generations.

# Jais in Inference Endpoints

You may need to add payment options at some stage. Other than that this is incredibly easy: 

1. Go to the Inference Endpoints enabled model: [derek-thomas/jais-13b-chat-hf](https://huggingface.co/derek-thomas/jais-13b-chat-hf) 
2. Click on `deploy` in the top right and choose `inference endpoints`
3. Choose your desired settings. I chose:
    1. Nvidia Tesla T4 4xGPU
    1. Scale to 0 after 15 minutes (Note this will put the endpoint to sleep after 15 min of inactivity. You will need to "wake" it up in this case [details here](https://huggingface.co/docs/inference-endpoints/autoscaling#scaling-to-0))
    1. Protected
4. Create Endpoint!

Use Jinja for convenient templating

In [12]:
from jinja2 import Template
# Define the Jinja template as a string
template_string = """
### Instruction: Use the following unique documents in the Context section to answer the Query at the end. If you don't know the answer, just say that you don't know, don't try to make up an answer. 
### Context 
{% for doc in documents %}
---
    {{ doc.content }}
{% endfor %}
---
[|AI|]:
### Query: [|Human|] {{query}}
### Response: [|AI|]
"""

# Create a Jinja Template object from the string
template = Template(template_string)

# Render the template with the data
whole_prompt = template.render(documents=documents, query=query)

# Print the rendered template
print(whole_prompt)



### Instruction: Use the following unique documents in the Context section to answer the Query at the end. If you don't know the answer, just say that you don't know, don't try to make up an answer. 
### Context 

---
    كونمينغ ؛ (بينيين Kūnmíng)؛ ، المعروفة أيضا باسم يونان-فو ، هي أكبر مدينة وعاصمة مقاطعة يونان في الصين. وتعتبر المركز السياسي والاقتصادي والاتصالاتي والثقافي للمقاطعة إلى جانب كونها مقر حكومة المقاطعة. يقع المقر الرئيسي للعديد من الشركات الكبيرة في محافظة يونان في كونمينغ. كانت المدينة مهمة خلال الحرب العالمية الثانية كمركز عسكري صيني، وقاعدة جوية أمريكية ومحطة نقل لطريق بورما. توجد كونمينغ في منتصف هضبة يونان-قويتشو على ارتفاع 1900 متر (6234 قدم) فوق مستوى سطح البحر وبين خطوط العرض إلى الشمال مباشرة من مدار السرطان. بلغ عدد سكان كونمينغ 8,460,088 نسمة في تعداد 2020. وكان عدد سكانها في المناطق الحضرية التابعة لها 4,089,100 في تقديرات 2018. كانت المنطقة المبنية (أو الحضرية) المكونة من جميع المناطق الحضرية، عدا جينينج غير المجمعة بعد، كانت موطنًا لـ3,779,900 نسمة. تقع 

In [13]:
import getpass
API_URL = getpass.getpass('API URL: ')
BEARER = getpass.getpass('Bearer Token: ')

API URL:  ········
Bearer Token:  ········


In [14]:
import requests

headers = {
	"Authorization": f"Bearer {BEARER}",
	"Content-Type": "application/json"
}

def call_jais(payload):
	response = requests.post(API_URL, headers=headers, json=payload)
	return response.json()
	

### RAG System Prompt

In [15]:
print(call_jais({'inputs': '', "prompt":whole_prompt}))


### Instruction: Use the following unique documents in the Context section to answer the Query at the end. If you don't know the answer, just say that you don't know, don't try to make up an answer. 
### Context 

---
    كونمينغ ؛ (بينيين Kūnmíng)؛ ، المعروفة أيضا باسم يونان-فو ، هي أكبر مدينة وعاصمة مقاطعة يونان في الصين. وتعتبر المركز السياسي والاقتصادي والاتصالاتي والثقافي للمقاطعة إلى جانب كونها مقر حكومة المقاطعة. يقع المقر الرئيسي للعديد من الشركات الكبيرة في محافظة يونان في كونمينغ. كانت المدينة مهمة خلال الحرب العالمية الثانية كمركز عسكري صيني، وقاعدة جوية أمريكية ومحطة نقل لطريق بورما. توجد كونمينغ في منتصف هضبة يونان-قويتشو على ارتفاع 1900 متر (6234 قدم) فوق مستوى سطح البحر وبين خطوط العرض إلى الشمال مباشرة من مدار السرطان. بلغ عدد سكان كونمينغ 8,460,088 نسمة في تعداد 2020. وكان عدد سكانها في المناطق الحضرية التابعة لها 4,089,100 في تقديرات 2018. كانت المنطقة المبنية (أو الحضرية) المكونة من جميع المناطق الحضرية، عدا جينينج غير المجمعة بعد، كانت موطنًا لـ3,779,900 نسمة. تقع 